## Setup

In [0]:
%pip install yfinance -qq

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
spark.sql('USE CATALOG cscie103_catalog_final')

DataFrame[]

In [0]:
county_name_mapping = {
0:"HARJUMAA",
1:"HIIUMAA",
2:"IDA-VIRUMAA",
3:"JÄRVAMAA",
4:"JÕGEVAMAA",
5:"LÄÄNE-VIRUMAA",
6:"LÄÄNEMAA",
7:"PÄRNUMAA",
8:"PÕLVAMAA",
9:"RAPLAMAA",
10:"SAAREMAA",
11:"TARTUMAA",
12:"UNKNOWN",
13:"VALGAMAA",
14:"VILJANDIMAA",
15:"VÕRUMAA"
}
product_tyupe_mapping = {0: "Combined", 1: "Fixed", 2: "General service", 3: "Spot"}


In [0]:
#Join client with county and product mapping cand create a materialized view
# first let's turn the mapping into a spark dataframe and save it as a table
county_df=spark.createDataFrame(county_name_mapping.items(), ["county_id", "county_name"])
county_df.write.mode("overwrite").saveAsTable("silver.county_mapping")
product_df=spark.createDataFrame(product_tyupe_mapping.items(), ["product_id", "product_type"])
product_df.write.mode("overwrite").saveAsTable("silver.product_mapping")

## Now, we populate silver with clean and modeled materialized views

In [0]:
%sql
select county, count(*) as qt from bronze.weather_mapping where county is not null group by county order by 1;

county qt 0 6 1 1 2 4 3 3 4 3 5 4 6 2 7 5 8 1 9 3 10 4 11 4 13 1 14 3 15 5

**It appears that there are no weather stations in the unknown county 12, which makes sense.**

In [0]:
%sql
select max(datetime), min(datetime) from bronze.train 
union all
select max(forecast_date), min(forecast_date) from bronze.gas_prices
union all
select max(origin_date), min(origin_date) from bronze.gas_prices
union all
select max(forecast_date), min(forecast_date) from bronze.electricity_prices
union all
select max(origin_date), min(origin_date) from bronze.electricity_prices


max(datetime) min(datetime) 2023-05-31T23:00:00.000Z 2021-09-01T00:00:00.000Z 2023-05-30T23:00:00.000Z 2021-09-01T00:00:00.000Z 2023-05-29T23:00:00.000Z 2021-08-31T00:00:00.000Z 2023-05-30T00:00:00.000Z 2021-09-01T00:00:00.000Z 2023-05-29T00:00:00.000Z 2021-08-31T00:00:00.000Z

In [0]:
%sql
select 
county_id, 
county_name,
count(*) as station_count,
st_union_agg(st_point(longitude, latitude)) as county_stations,
st_centroid(county_stations) as county_centroid, 
st_x(county_centroid) as county_centroid_longitude, 
st_y(county_centroid) as county_centroid_latitude
from silver.weather_mapping_mv 
where county_id is not null 
group by county_id, county_name
;

county_id county_name station_count county_stations county_centroid county_centroid_longitude county_centroid_latitude 2 IDA-VIRUMAA 4 MULTIPOINT((27.7 59.399999999999984),(27.2 59.09999999999999),(27.7 59.09999999999999),(27.2 59.399999999999984)) POINT(27.45 59.249999999999986) 27.45 59.249999999999986 0 HARJUMAA 6 MULTIPOINT((25.2 59.09999999999999),(24.7 59.399999999999984),(24.2 59.09999999999999),(25.7 59.399999999999984),(25.2 59.399999999999984),(24.2 59.399999999999984)) POINT(24.866666666666664 59.29999999999998) 24.866666666666664 59.29999999999998 15 VÕRUMAA 5 MULTIPOINT((27.2 57.9),(27.2 57.6),(27.7 57.9),(26.7 57.6),(26.7 57.9)) POINT(27.1 57.779999999999994) 27.1 57.779999999999994 11 TARTUMAA 4 MULTIPOINT((27.2 58.49999999999999),(26.7 58.2),(26.7 58.49999999999999),(26.2 58.2)) POINT(26.7 58.349999999999994) 26.7 58.349999999999994 5 LÄÄNE-VIRUMAA 4 MULTIPOINT((26.2 59.399999999999984),(26.7 59.09999999999999),(26.7 59.399999999999984),(26.2 59.09999999999999)) POINT(26.45 59.249999999999986) 26.45 59.249999999999986 7 PÄRNUMAA 5 MULTIPOINT((23.7 58.49999999999999),(24.7 58.2),(24.2 58.49999999999999),(24.7 58.49999999999999),(25.2 58.2)) POINT(24.5 58.379999999999995) 24.5 58.379999999999995 6 LÄÄNEMAA 2 MULTIPOINT((23.7 59.09999999999999),(23.7 58.79999999999999)) POINT(23.7 58.94999999999999) 23.7 58.94999999999999 13 VALGAMAA 1 POINT(26.2 57.9) POINT(26.2 57.9) 26.2 57.9 10 SAAREMAA 4 MULTIPOINT((22.2 58.2),(22.2 58.49999999999999),(22.7 58.49999999999999),(23.2 58.49999999999999)) POINT(22.575 58.425) 22.575 58.425 14 VILJANDIMAA 3 MULTIPOINT((25.7 58.2),(25.2 58.49999999999999),(25.7 58.49999999999999)) POINT(25.53333333333333 58.4) 25.53333333333333 58.4 4 JÕGEVAMAA 3 MULTIPOINT((26.2 58.79999999999999),(26.7 58.79999999999999),(26.2 58.49999999999999)) POINT(26.366666666666664 58.69999999999999) 26.366666666666664 58.69999999999999 9 RAPLAMAA 3 MULTIPOINT((24.7 58.79999999999999),(24.7 59.09999999999999),(24.2 58.79999999999999)) POINT(24.53333333333333 58.899999999999984) 24.53333333333333 58.899999999999984 8 PÕLVAMAA 1 POINT(27.2 58.2) POINT(27.2 58.2) 27.2 58.2 1 HIIUMAA 1 POINT(22.7 58.79999999999999) POINT(22.7 58.79999999999999) 22.7 58.79999999999999 3 JÄRVAMAA 3 MULTIPOINT((25.2 58.79999999999999),(25.7 58.79999999999999),(25.7 59.09999999999999)) POINT(25.53333333333333 58.899999999999984) 25.53333333333333 58.899999999999984

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE VIEW cscie103_catalog_final.silver.county_geo AS
SELECT 
county_id, 
county_name,
count(*) as station_count,
st_union_agg(st_point(longitude, latitude)) as county_stations,
st_centroid(county_stations) as county_centroid, 
st_x(county_centroid) as county_longitude, 
st_y(county_centroid) as county_latitude
from cscie103_catalog_final.silver.weather_mapping_mv 
where county_id is not null 
group by county_id, county_name
;

In [0]:
%sql
CREATE OR REPLACE TABLE cscie103_catalog_final.silver.county_map AS
SELECT 
county_id, 
county_name,
station_count,
county_longitude as longitude, 
county_latitude as latitude
from cscie103_catalog_final.silver.county_geo 
;

num_affected_rows num_inserted_rows

In [0]:
%sql
SELECT 
cg.county_id, 
cg.county_name,
county_longitude, 
county_latitude,
wh.data_block_id, 
TO_DATE(wh.datetime, "yyyy-MM-dd") AS wh_observ_date,
FLOOR(EXTRACT(HOUR FROM wh.datetime) / 4) AS wh_observ_4hour,
TO_DATE(wf.forecast_datetime, "yyyy-MM-dd") AS wf_observ_date,
FLOOR(EXTRACT(HOUR FROM wf.forecast_datetime) / 4) AS wf_observ_4hour,
AVG(wh.temperature) AS wh_temperature, 
AVG(wh.dewpoint) AS wh_dewpoint, 
AVG(wh.snowfall) AS wh_snowfall, 
AVG(wh.surface_pressure) AS wh_surface_pressure, 
AVG(wh.cloudcover_total) AS wh_cloudcover_total,
AVG(wh.cloudcover_low) AS wh_cloudcover_low,
AVG(wh.cloudcover_mid) AS wh_cloudcover_mid,
AVG(wh.cloudcover_high) AS wh_cloudcover_high,
AVG(wh.windspeed_10m) AS wh_windspeed_10m,
AVG(wh.winddirection_10m) AS wh_winddirection_10m,
AVG(wh.shortwave_radiation) AS wh_shortwave_radiation,
AVG(wh.direct_solar_radiation) AS wh_direct_solar_radiation,
AVG(wh.diffuse_radiation) AS wh_diffuse_radiation,
AVG(wf.temperature) AS wf_temperature,
AVG(wf.dewpoint) AS wf_dewpoint,
AVG(wf.cloudcover_high) AS wf_cloudcover_high,
AVG(wf.cloudcover_low) AS wf_cloudcover_low,
AVG(wf.cloudcover_mid) AS wf_cloudcover_mid,
AVG(wf.cloudcover_total) AS wf_cloudcover_total,
AVG(wf.10_metre_u_wind_component) AS wf_10_metre_u_wind_component,
AVG(wf.10_metre_v_wind_component) AS wf_10_metre_v_wind_component,
AVG(wf.dewpoint) AS wf_dewpoint,
AVG(wf.cloudcover_total) AS wf_cloudcover_total,
AVG(wf.10_metre_u_wind_component) AS wf_10_metre_u_wind_component,
AVG(wf.10_metre_v_wind_component) AS wf_10_metre_v_wind_component,
AVG(wf.direct_solar_radiation) AS wf_direct_solar_radiation,
AVG(wf.surface_solar_radiation_downwards) AS wf_surface_solar_radiation_downwards,
AVG(wf.snowfall) AS wf_snowfall,
AVG(wf.total_precipitation) AS wf_total_precipitation
FROM cscie103_catalog_final.gold.county_geo cg INNER JOIN cscie103_catalog_final.silver.weather_hist_stream wh ON 
cg.county_id = wh.county INNER JOIN cscie103_catalog_final.silver.weather_forecast_stream wf ON 
cg.county_id = wf.county and wh.data_block_id = wf.data_block_id 
--AND wh.datetime = wf.forecast_datetime
GROUP BY county_id, cg.county_name, county_longitude, county_latitude, wh.data_block_id, wh_observ_date, wh_observ_4hour

county_id county_name county_longitude county_latitude data_block_id wh_observ_date wh_observ_4hour wh_temperature wh_dewpoint wh_snowfall wh_surface_pressure wh_cloudcover_total wh_cloudcover_low wh_cloudcover_mid wh_cloudcover_high wh_windspeed_10m wh_winddirection_10m wh_shortwave_radiation wh_direct_solar_radiation wh_diffuse_radiation wf_temperature wf_dewpoint wf_cloudcover_high wf_cloudcover_low wf_cloudcover_mid wf_cloudcover_total wf_10_metre_u_wind_component wf_10_metre_v_wind_component wf_dewpoint wf_cloudcover_total wf_10_metre_u_wind_component wf_10_metre_v_wind_component wf_direct_solar_radiation wf_surface_solar_radiation_downwards wf_snowfall wf_total_precipitation 10 SAAREMAA 22.575 58.425 260.0 2022-05-18 2 8.933333333333332 1.7666666666666666 0.0 1023.0333333333333 10.0 0.3333333333333333 0.0 32.666666666666664 5.333333333333333 153.33333333333334 500.3333333333333 406.3333333333333 94.0 9.101464843750023 3.428084309895856 0.6142634091277918 0.0 1.48773193359375E-4 0.6142731520036856 5.222257932027181 -1.7759157816569011 3.428084309895856 0.6142731520036856 5.222257932027181 -1.7759157816569011 764.9621238425925 502.99193287037036 0.0 0.0 10 SAAREMAA 22.575 58.425 275.0 2022-06-02 0 10.6 9.9 0.0 1001.7 100.0 100.0 30.0 87.0 3.5555555555555554 302.0 0.0 0.0 0.0 10.592187500000023 9.808984375000023 0.99578857421875 1.0 1.0 0.999995868653059 -2.6251707077026367 3.3794450759887695 9.808984375000023 0.999995868653059 -2.6251707077026367 3.3794450759887695 0.0 0.0 0.0 0.0 8 PÕLVAMAA 27.2 58.2 396.0 2022-10-01 2 7.099999999999999 6.433333333333334 0.0 1010.6666666666666 100.0 67.0 68.0 98.0 2.037037037037037 296.3333333333333 132.66666666666666 31.333333333333332 101.33333333333333 7.390242513020856 5.659143066406273 0.987152099609375 0.0067138671875 0.4211018880208333 0.9874064127604166 -1.313905398050944 1.1526172757148743 5.659143066406273 0.9874064127604166 -1.313905398050944 1.1526172757148743 390.96740740740734 194.62378106011283 0.0 0.0 11 TARTUMAA 26.7 58.349999999999994 419.0 2022-10-24 2 3.0499999999999994 2.0833333333333335 0.0 1003.8833333333336 13.0 13.0 2.1666666666666665 0.0 1.1944444444444444 75.16666666666667 85.66666666666667 44.0 41.666666666666664 2.4664957682291893 1.974837239583356 0.0 0.4214426676432292 0.040191650390625 0.4457499186197917 -0.20069154103597006 -0.5901638666788737 1.974837239583356 0.4457499186197917 -0.20069154103597006 -0.5901638666788737 261.6 93.58375578703703 0.0 0.0 10 SAAREMAA 22.575 58.425 424.0 2022-10-29 0 11.6 11.1 0.0 1006.6 100.0 100.0 2.0 97.0 5.277777777777778 205.0 0.0 0.0 0.0 11.818261718750023 11.048059082031273 0.9851009249687195 0.999996155500412 0.2418212890625 1.000001609325409 5.054187893867493 2.2451544404029846 11.048059082031273 1.000001609325409 5.054187893867493 2.2451544404029846 0.0 0.0 0.0 0.0 10 SAAREMAA 22.575 58.425 466.0 2022-12-10 2 -1.9333333333333333 -3.8333333333333335 0.07 1005.6999999999999 51.0 24.0 48.666666666666664 0.0 6.305555555555556 260.0 3.6666666666666665 0.6666666666666666 3.0 -3.0589355468749773 -4.81805013020831 0.010050455729166666 0.5515244950850805 0.9331868489583334 0.9697758555412292 0.5517231623331705 6.838449478149414 -4.81805013020831 0.9697758555412292 0.5517231623331705 6.838449478149414 16.008888888888887 19.954014395254628 2.133064410045904E-4 2.1298726399739584E-4 15 VÕRUMAA 27.1 57.779999999999994 164.0 2022-02-11 1 -0.48999999999999977 -1.4500000000000008 0.0 990.9149999999998 67.15 67.15 4.85 13.6 5.043055555555555 197.9 0.0 0.0 0.0 -0.8873840332031022 -1.8084594726562273 0.0 0.974371337890625 0.0 0.974371337890625 4.718692016601563 1.6189579010009765 -1.8084594726562273 0.974371337890625 4.718692016601563 1.6189579010009765 0.02834722222222222 0.0 9.916722774505615E-7 1.0333955287933349E-6 10 SAAREMAA 22.575 58.425 484.0 2022-12-28 1 1.625 -1.875 0.0 1005.0999999999999 21.75 21.75 3.5 0.0 6.604166666666667 268.5 0.0 0.0 0.0 1.9925476074218977 -1.9183563232421648 0.12438583374023438 0.164215087890625 0.06744

**Note: if the latitude and longitude values are identical to 12 decimal places, they are the identical point on earth**

In [0]:
%sql
select count (distinct county_id) from cscie103_catalog_final.gold.county_weather_4hours_mv
union all 
select count (distinct county_id) from cscie103_catalog_final.gold.county_energy_4hours_mv
union all
select count (distinct county) from cscie103_catalog_final.silver.weather_forecast_stream
union all
select count (distinct county) from cscie103_catalog_final.silver.weather_forecast
union all
select count (distinct county) from cscie103_catalog_final.bronze.weather_forecast wf inner join
cscie103_catalog_final.bronze.weather_mapping wm on  round(wf.latitude,13)=round(wm.latitude, 13) and round(wf.longitude, 13)=round(wm.longitude,13)
union all
select count (distinct county_id) from cscie103_catalog_final.silver.weather_forecast_mv;
;
    


count(DISTINCTcounty_id) 7 15 7 7 15 15

In [0]:
%sql
select count (distinct county_id) from cscie103_catalog_final.silver.weather_hist_mv
union all
select count (distinct county_id) from cscie103_catalog_final.silver.weather_forecast_mv;


count(DISTINCTcounty_id) 15 15

In [0]:
%sql
SELECT 
t.county_id, 
t.county_name,
cm.latitude,
cm.longitude,
t.is_business,
t.is_consumption,
t.product_type_id,
t.product_type,
c.installed_capacity,
c.eic_count,
t.target,
ep.euros_per_mwh,
gp.highest_price_per_mwh,
gp.lowest_price_per_mwh,
t.datetime,
TO_DATE(t.datetime) as t_observ_date,
FLOOR(EXTRACT(HOUR FROM t.datetime)/4) as t_observ_4hour,
c.observ_date as c_observ_date,
gp.forecast_date as gp_forecast_date,
gp.origin_date as gp_origin_date,
ep.forecast_date as ep_forecast_date,
ep.origin_date as ep_origin_date,
t.data_block_id,
t.row_id,
t.prediction_unit_id
FROM cscie103_catalog_final.silver.train_mv t INNER JOIN cscie103_catalog_final.silver.client_mv c
ON t.county_id = c.county_id 
AND t.product_type_id = c.product_type_id
AND t.is_business = c.is_business
AND t.data_block_id = c.data_block_id 
INNER JOIN cscie103_catalog_final.silver.gas_prices_mv gp
ON t.data_block_id = gp.data_block_id 
INNER JOIN cscie103_catalog_final.silver.electricity_prices_mv ep
ON t.data_block_id = ep.data_block_id 
AND EXTRACT(HOUR FROM t.datetime)=EXTRACT(HOUR FROM ep.forecast_date)
INNER JOIN cscie103_catalog_final.silver.county_map cm
ON t.county_id = cm.county_id
order by row_id
limit 100
    

county_id county_name latitude longitude installed_capacity eic_count is_business target is_consumption product_type_id product_type euros_per_mwh highest_price_per_mwh lowest_price_per_mwh datetime t_observ_date t_observ_4hour c_observ_date gp_forecast_date gp_origin_date ep_forecast_date ep_origin_date data_block_id row_id prediction_unit_id 0 HARJUMAA 59.29999999999998 24.866666666666664 952.89 108 false 0.793 false 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5856 0 0 HARJUMAA 59.29999999999998 24.866666666666664 952.89 108 false 107.129 true 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5857 0 0 HARJUMAA 59.29999999999998 24.866666666666664 166.4 17 false 0.0 false 2 General service 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5858 1 0 HARJUMAA 59.29999999999998 24.866666666666664 166.4 17 false 19.63 true 2 General service 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5859 1 0 HARJUMAA 59.29999999999998 24.866666666666664 7207.88 688 false 0.977 false 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5860 2 0 HARJUMAA 59.29999999999998 24.866666666666664 7207.88 688 false 690.908 true 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5861 2 0 HARJUMAA 59.29999999999998 24.866666666666664 400.0 5 true 0.0 false 0 Combined 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5862 3 0 HARJUMAA 59.29999999999998 24.866666666666664 400.0 5 true 64.1 true 0 Combined 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5863 3 0 HARJUMAA 59.29999999999998 24.866666666666664 1411.0 43 true 0.0 false 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5864 4 0 HARJUMAA 59.29999999999998 24.866666666666664 1411.0 43 true 529.972 true 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5865 4 0 HARJUMAA 59.29999999999998 24.866666666666664 13417.79 265 true 0.449 false 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5866 5 0 HARJUMAA 59.29999999999998 24.866666666666664 13417.79 265 true 4283.111 true 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5867 5 1 HIIUMAA 58.79999999999999 22.7 80.0 7 false 0.0 false 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5868 6 1 HIIUMAA 58.79999999999999 22.7 80.0 7 false 2.741 true 1 Fixed 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5869 6 1 HIIUMAA 58.79999999999999 22.7 472.6 42 false 0.107 false 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5870 7 1 HIIUMAA 58.79999999999999 22.7 472.6 42 false 26.987 true 3 Spot 96.99 46.29 45.62 2021-09-03T00:00:00.000Z 2021-09-03 0 2021-09-01 2021-09-02 2021-09-01 2021-09-02T00:00:00.000Z 2021-09-01T00:00:00.000Z 2 5871